In [4]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

import folium
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import math
import random
from datetime import timedelta

import warnings
warnings.filterwarnings('ignore')
cnf = '#393e46'
dth = '#ff2e63'
rec = '#21bf73'
act = '#fe9801'

In [5]:
import plotly as py
py.offline.init_notebook_mode(connected=True)

In [52]:
df = pd.read_csv('Covid-19-Preprocessed-Dataset/preprocessed/covid_19_data_cleaned.csv', parse_dates=['Date'])
country_daywise = pd.read_csv('Covid-19-Preprocessed-Dataset/preprocessed/country_daywise.csv', parse_dates=['Date'])
countrywise = pd.read_csv('Covid-19-Preprocessed-Dataset/preprocessed/countrywise.csv')
daywise = pd.read_csv('Covid-19-Preprocessed-Dataset/preprocessed/daywise.csv', parse_dates=['Date'])

In [54]:
df['Province/State'] = df['Province/State'].fillna("")
df.head()

Date Province/State      Country   Lat  Long  Confirmed  Recovered  \
0 2020-01-22                 Afghanistan  33.0  65.0          0          0   
1 2020-01-23                 Afghanistan  33.0  65.0          0          0   
2 2020-01-24                 Afghanistan  33.0  65.0          0          0   
3 2020-01-25                 Afghanistan  33.0  65.0          0          0   
4 2020-01-26                 Afghanistan  33.0  65.0          0          0   

   Deaths  Active  
0       0       0  
1       0       0  
2       0       0  
3       0       0  
4       0       0

In [55]:
confirmed = df.groupby('Date').sum()['Confirmed'].reset_index()
recovered = df.groupby('Date').sum()['Recovered'].reset_index()
deaths = df.groupby('Date').sum()['Deaths'].reset_index()
deaths.head()

Date  Deaths
0 2020-01-22      17
1 2020-01-23      18
2 2020-01-24      26
3 2020-01-25      42
4 2020-01-26      56

In [18]:
df.isnull().sum()

Date              0
Province/State    0
Country           0
Lat               0
Long              0
Confirmed         0
Recovered         0
Deaths            0
Active            0
dtype: int64

In [19]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 29430 entries, 0 to 29429
Data columns (total 9 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Date            29430 non-null  datetime64[ns]
 1   Province/State  29430 non-null  object        
 2   Country         29430 non-null  object        
 3   Lat             29430 non-null  float64       
 4   Long            29430 non-null  float64       
 5   Confirmed       29430 non-null  int64         
 6   Recovered       29430 non-null  int64         
 7   Deaths          29430 non-null  int64         
 8   Active          29430 non-null  int64         
dtypes: datetime64[ns](1), float64(2), int64(4), object(2)
memory usage: 2.0+ MB


In [21]:
df.query('Country == "US"')

Date Province/State Country      Lat     Long  Confirmed  \
24525 2020-01-22                     US  37.0902 -95.7129          1   
24526 2020-01-23                     US  37.0902 -95.7129          1   
24527 2020-01-24                     US  37.0902 -95.7129          2   
24528 2020-01-25                     US  37.0902 -95.7129          2   
24529 2020-01-26                     US  37.0902 -95.7129          5   
...          ...            ...     ...      ...      ...        ...   
24629 2020-05-05                     US  37.0902 -95.7129    1204351   
24630 2020-05-06                     US  37.0902 -95.7129    1229331   
24631 2020-05-07                     US  37.0902 -95.7129    1257023   
24632 2020-05-08                     US  37.0902 -95.7129    1283929   
24633 2020-05-09                     US  37.0902 -95.7129    1309550   

       Recovered  Deaths   Active  
24525          0       0        1  
24526          0       0        1  
24527          0       0        2  
24528          0       0        2  
24529          0       0        5  
...          ...     ...      ...  
24629     189791   71064   943496  
24630     189910   73455   965966  
24631     195036   75662   986325  
24632     198993   77180  1007756  
24633     212534   78795  1018221  

[109 rows x 9 columns]

In [29]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=confirmed['Date'], y=confirmed['Confirmed'], mode='lines+markers', name='Confirmed', line= dict(color='Orange')))
fig.add_trace(go.Scatter(x=confirmed['Date'], y=recovered['Recovered'], mode='lines+markers', name='Recovered', line= dict(color='Green')))
fig.add_trace(go.Scatter(x=confirmed['Date'], y=deaths['Deaths'], mode='lines+markers', name='Deaths', line= dict(color='Red')))
fig.update_layout(title='Worldwide covid-19 cases')
fig.show()

In [30]:
df['Date'] = df['Date'].astype(str)

In [34]:
fig = px.density_mapbox(df, lat='Lat', lon='Long', hover_name='Country', hover_data=['Confirmed', 'Recovered', 'Deaths'], animation_frame='Date', color_continuous_scale='Portland', radius=7, zoom=0, height=700)
fig.update_layout(title='Worlwide Covid-19 Cases with TL')
fig.update_layout(mapbox_style='open-street-map', mapbox_center_lon=0)
fig.show()

In [35]:
df['Date'] = pd.to_datetime(df['Date'])

In [59]:
ship_rows = df['Province/State'].str.contains('Grand Princess') | df['Province/State'].str.contains('Diamond Princess') | df['Country'].str.contains('Grand Princess') | df['Country'].str.contains('Diamond Princess') | df['Country'].str.contains('MS Zaandam')
ship = df[ship_rows]

df = df[~ship_rows]
ship

Date Province/State           Country  Lat  Long  Confirmed  \
9592  2020-01-22                 Diamond Princess  0.0   0.0          0   
9593  2020-01-23                 Diamond Princess  0.0   0.0          0   
9594  2020-01-24                 Diamond Princess  0.0   0.0          0   
9595  2020-01-25                 Diamond Princess  0.0   0.0          0   
9596  2020-01-26                 Diamond Princess  0.0   0.0          0   
...          ...            ...               ...  ...   ...        ...   
27572 2020-05-05                       MS Zaandam  0.0   0.0          9   
27573 2020-05-06                       MS Zaandam  0.0   0.0          9   
27574 2020-05-07                       MS Zaandam  0.0   0.0          9   
27575 2020-05-08                       MS Zaandam  0.0   0.0          9   
27576 2020-05-09                       MS Zaandam  0.0   0.0          9   

       Recovered  Deaths  Active  
9592           0       0       0  
9593           0       0       0  
9594           0       0       0  
9595           0       0       0  
9596           0       0       0  
...          ...     ...     ...  
27572          0       2       7  
27573          0       2       7  
27574          0       2       7  
27575          0       2       7  
27576          0       2       7  

[327 rows x 9 columns]

In [60]:
ship_latest = ship[ship['Date'] == max(ship['Date'])]
ship_latest

Date    Province/State           Country  Lat  Long  Confirmed  \
9700  2020-05-09                    Diamond Princess  0.0   0.0        712   
25287 2020-05-09  Diamond Princess            Canada  0.0   0.0          1   
27576 2020-05-09                          MS Zaandam  0.0   0.0          9   

       Recovered  Deaths  Active  
9700         645      13      54  
25287          0       1       0  
27576          0       2       7

In [61]:
ship_latest.style.background_gradient(cmap='Pastel1_r')

In [64]:
temp = df.groupby('Date')['Confirmed','Deaths','Recovered','Active'].sum().reset_index()
temp = temp[temp['Date'] == max(temp['Date'])].reset_index(drop=True)
tm = temp.melt(id_vars='Date', value_vars=['Active', 'Deaths', 'Recovered']) 
fig = px.treemap(tm, path= ['variable'], values='value', height=250, width=800, color_discrete_sequence=[act,rec,dth])
fig.data[0].textinfo = 'label+text+value'
fig.show()

In [69]:
temp = df.groupby('Date')['Recovered', 'Deaths', 'Active'].sum().reset_index()
temp = temp.melt(id_vars='Date', value_vars = ['Recovered', 'Deaths', 'Active'], var_name='Case', value_name='Count')
fig = px.area(temp, x='Date', y='Count', color='Case', height=600, title='Cases over time', color_discrete_sequence=[act,rec,dth])
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

In [72]:
temp = df[df['Date']==max(df['Date'])]
m = folium.Map(location=[0,0], tiles='cartodbpositron', min_zoom=1, max_zoom=4, zoom_start=1)
for i in range(0, len(temp)):
    folium.Circle(location=[temp.iloc[i]['Lat'], temp.iloc[i]['Long']], color='crimson', fill='crimson', 
                  tooltip='<li><bold>Country:' + str(temp.iloc[i]['Country'])+
                            '<li><bold>Province:' + str(temp.iloc[i]['Province/State'])+
                             '<li><bold>Confirmed:' + str(temp.iloc[i]['Confirmed'])+
                                 '<li><bold>Deaths:' + str(temp.iloc[i]['Deaths']), radius=int(temp.iloc[i]['Confirmed'])**0.5).add_to(m)
m

In [76]:
fig = px.choropleth(country_daywise, locations='Country', locationmode='country names', color=np.log(country_daywise['Confirmed']),
                   hover_name='Country', animation_frame=country_daywise['Date'].dt.strftime('%Y-%m-%d'), title='Cases over time',
                   color_continuous_scale=px.colors.sequential.Inferno)
fig.update(layout_coloraxis_showscale = True)
fig.show()

In [78]:
fig_c = px.bar(daywise, x='Date', y='Confirmed', color_discrete_sequence=[act])
fig_d = px.bar(daywise, x='Date', y='Deaths', color_discrete_sequence=[dth])
fig = make_subplots(rows=1, cols=2, shared_xaxes=False, horizontal_spacing=0.1, subplot_titles=('Confirmed Cases', 'Deaths Cases'))

fig.add_trace(fig_c['data'][0], row=1, col=1)
fig.add_trace(fig_d['data'][0], row=1, col=2)
fig.update_layout(height=480)
fig.show()

In [80]:
fig_c = px.choropleth(countrywise, locations='Country', locationmode='country names', color=np.log(countrywise['Confirmed']),
                     hover_name='Country', hover_data=['Confirmed'])

temp = countrywise[countrywise['Deaths'] > 0]
fig_d = px.choropleth(, locations='Country', locationmode='country names', color=np.log(countrywise['Deaths']),
                     hover_name='Country', hover_data=['Death'])

fig = make_subplots(rows=1, cols=2, subplot_titles=['Confirmed', 'Deaths'], specs= [[{'type': 'choropleth'}, {'type': 'choropleth'}]])
fig.add_trace(fig_c['data'][0], row=1,col=1)
fig.add_trace(fig_d['data'][0], row=1,col=2)
fig.show()

ValueError: Value of 'hover_data_0' is not the name of a column in 'data_frame'. Expected one of ['Country', 'Confirmed', 'Deaths', 'Recovered', 'Active', 'New Cases', 'Deaths / 100 Cases', 'Recovered / 100 Cases', 'Deaths / 100 Recovered', 'Population', 'Cases / Million People', 'Confirmed last week', '1 week change', '1 week % increase'] but received: Death